In [1]:
from langchain.vectorstores import Chroma
from langchain.embeddings.sentence_transformer import SentenceTransformerEmbeddings
from langchain.chains import VectorDBQA
from langchain_community.llms import Ollama
import sentence_transformers
import pandas as pd
import time
from collections import defaultdict

/Volumes/External/opt/anaconda3/envs/nlp_ollama2/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
%cd /Volumes/External/source/GTPracticum/data 

/Volumes/External/source/GTPracticum/data


/Volumes/External/opt/anaconda3/envs/nlp_ollama2/lib/python3.11/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [4]:
results_df=pd.read_csv('enron_labeled_curated.csv')


In [5]:
results_df.head(1).T

0
search_phrase                  mark to market accounting practices
label                                                            0
email            Subject: Re: WSJ Article on Enron's Mark to Ma...
mistral_pred                                                   0.0
openhermes_pred                                                0.0
vicuna_pred                                                    0.8
gemma_pred                                                     0.0

In [6]:
results_df['label'].value_counts()

label
0    2404
1     391
Name: count, dtype: int64

In [1]:
from langchain.vectorstores import Chroma
from langchain.embeddings.sentence_transformer import SentenceTransformerEmbeddings
from langchain.chains import VectorDBQA
from langchain_community.llms import Ollama
import sentence_transformers
import pandas as pd
import time
from collections import defaultdict

/Volumes/External/opt/anaconda3/envs/nlp_ollama2/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
%cd /Volumes/External/source/GTPracticum/data 

/Volumes/External/source/GTPracticum/data


/Volumes/External/opt/anaconda3/envs/nlp_ollama2/lib/python3.11/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [80]:
x=[{"email_text":"I'm concerned that the mark to market accounting practices that we placed the loses in the Raptor SBE could be viewed as Fraud","reason":"The email shows concern that the accounting practices could be viewed as fraud","Score":10},
   {"email_text":"I'm concerned that the mark to market accounting practices that we placed the loses in the Raptor SBE could be viewed as Fraud","reason":"The email shows concern that the accounting practices could be viewed as fraud","Score":10}]
json.dumps(x)

'[{"email_text": "I\'m concerned that the mark to market accounting practices that we placed the loses in the Raptor SBE could be viewed as Fraud", "reason": "The email shows concern that the accounting practices could be viewed as fraud", "Score": 10}, {"email_text": "I\'m concerned that the mark to market accounting practices that we placed the loses in the Raptor SBE could be viewed as Fraud", "reason": "The email shows concern that the accounting practices could be viewed as fraud", "Score": 10}]'

In [76]:
test_df=results_df[results_df['label']==1]
# test_df['test']=0
# for i,j in test_df.iterrows():
#     test_df.loc[test_df.index == i, 'test'] =1
# #     test_df.loc[test_df.iloc[i].name, 'test'] = 1
test_df

search_phrase  label  \
10    mark to market accounting practices      1   
13    mark to market accounting practices      1   
15    mark to market accounting practices      1   
18    mark to market accounting practices      1   
22    mark to market accounting practices      1   
...                                   ...    ...   
1817                               RANDOM      1   
2151                               RANDOM      1   
2506                               RANDOM      1   
2507                               RANDOM      1   
2508                               RANDOM      1   

                                                  email  mistral_pred  \
10    Investors are asking hard questions, and not a...           0.0   
13    Subject: The first detailed allegations that E...           1.0   
15    ancial reporting technique called mark-to-mark...           1.0   
18    ng more disclosures about the accounting used,...           0.7   
22    "There could be a quality-of-earnings issue," ...           0.5   
...                                                 ...           ...   
1817  Subject: bookouts in discussion\n\nBill,\n\nPe...           0.0   
2151  Subject: \n\nMark, this is great - giving the ...           0.0   
2506  -bid & to prevent market manipulation.\n  \n  ...           0.5   
2507  n are causing loss to \nEnron by, what we beli...           0.5   
2508   London Commercial Court \ncould be swayed by ...           0.7   

      openhermes_pred  vicuna_pred  gemma_pred  
10                0.0          0.7         0.2  
13                0.8          0.9         0.0  
15                0.7          0.9         0.8  
18                0.5          0.7         0.8  
22                0.5          0.8         0.2  
...               ...          ...         ...  
1817              0.0          0.7         0.2  
2151              0.0          0.7         0.0  
2506              0.0          0.8         0.6  
2507              0.5          0.9         0.6  
2508              0.0          0.8         0.6  

[391 rows x 7 columns]

In [81]:
def scoreEmails(test_df,output_name='resultsl',model='llama3'):    
    topicResults=[]
    print("Querying llm")
    for i,j in test_df.iterrows():
        llm = Ollama(model=model,temperature=0)
        print(f"Querying llm {model}")
        prompt="""<s>[INST] <<sys>>
                    You are a finance specialist does the following email try to hide loses: These are the enron emails. They used SBE with the name of Raptors to hide loses using mark to market accounting so revenue was realized as profit. Do any of the following emails indicate an abuse of the accounting rules or use the Raptor SBE to hide losses. Please respond to each email with a number on the scale of 0 to 10. where 0 is no abuse while 10 is outright fraud. you output as a json text extractorusing the following format
                    Example of such a email in json format: <</sys>>
    [{"email_text":"I'm concerned that the mark to market accounting practices that we placed the loses in the Raptor SBE could be viewed as Fraud",
    "reason":"The email shows concern that the accounting practices could be viewed as fraud","Score":10},
    {"email_text":"I'm concerned that the mark to market accounting practices that we hide the loses in the Raptor SBE could be viewed as Fraud",
    {"reason":"The email shows concern that the Raptor SBE hiding loses could be viewed as fraud","Score":10},
    {"email_text":"Accounting practices  did not report losses so revenue was realized as profit hidding true financial position",
    {"reason":"The email shows concern that the accounting practices are hiding the true financal position of the company","Score":10},
    {"email_text":"Accounting practices  we placed on the books are 100% legal and trasparent",
    {"reason":"The email shows no concern, the accounting practices are legal and transparent","Score":0},
    {"email_text":"News about the accounting practices at Enron discuss devrivatives and mark to market accounting",
    "reason":"The email containing news reports not an action to commit fraud or hide loses","Score":0}]

    Please score the following email:
    {"email_text":" """+j['email']+'"} [/INST]'
        start_time = time.time()
        print(len(prompt),len(j['email']),j['email'])
        x=llm.invoke(prompt)
        print(x)
        test_df.loc[test_df.index == i, f'{model}_result'] =x
        #test_df.loc[test_df.index == i, 'reason'] =pr
        print("--- %s seconds ---" % (time.time() - start_time),i)



In [58]:
import re
def score(result):
        y=None
        if '<Score>' in result:
            if '<End Score>' in result:
                y=re.findall(r'<Score>(.*?)<End Score>', result)[0]
            elif '</Score>' in result:
                y=re.findall(r'<Score>(.*?)</Score>', result)[-1]
        elif '**Score:**' in result:
            y=re.findall(r'\*\*Score:\*\* \d+',result)[0][10:]
        elif '**Email Score:** ' in result:
            y=re.findall(r'\*Email Score:\*\* \d+',result)[0][16:]
        elif 'a score of ' in result:
            y=re.findall(r'a score of (.*?)',result)
        elif 'The email score is ' in result:
            y=re.findall(r'The email score is \d+',result)[10:]
        elif 'Score: ' in result:
            y=re.findall(r'Score: \d+',result)[-1][7:]
        elif '## Score for the email:' in result:
            numbers=re.findall(r'\d+', result)
            y=numbers[0]
        elif 'I would score this email as ' in result:
            numbers=re.findall(r'I would score this email as \d+', result)
            if len(numbers)==0:
                y=0
            else:
                y=numbers[0][28]
        else:    
            numbers=re.findall(r'\d+', result)
            if len(numbers)==0:
                y=0
            elif len(numbers)==1:
                y=numbers[0]
            else:               
                y=""
        if y is not None and isinstance(y,list):
            if len(y)==0:
                y=''
            else:
                y=y[0]
        if y=='':
            y=0
        try:
            y = int(y)
        except ValueError:
            print(y)
            y=0
        except TypeError:
            y=0
        reason=""
        for i in tmp.split('}'):
            j=i[3:].split(':')
            if 'reason' in j[0]:
                reason=j[1][1:-1]
            if 'Score' in j[0]:
                y=j[1]
        return y,reason

In [45]:
tmp="""{"email_text":"Investors are asking hard questions, and not always getting the answers they want. Using mark-to-market methods, a company calculates the fair market value of a commodity position - whether it's a contract, an option, a swap, etc. - at the time, even if the value of the position is realized over a longer period. The problem with this method is the actual cash a company realizes from the position might not be the same value the company calculated in its original assessment. Also, sometimes it isn't easy to calculate the fair value of the commodity position. This is particularly true in instances where the market for the commodity isn't liquid. Over time, companies with the highest level of disclosure regarding their mark-to-market gains will most likely trade at higher multiples to counterparts that provide little or no disclosure, said ABN AMRO Inc. analyst Paul Patterson. Encouragingly, it appears companies may already be responding to the call for added disclosure. According to a survey Patterson conducted, more companies with energy trading units were willing to disclose the details of their mark-to-market accounting practices during third-quarter conference calls compared with those in the second quarter. Patterson said he prefers earnings that are cash-based. \"All things being equal, we believe reported earnings that more closely reflect the timely realization of cash have a higher quality associated with them than earnings that do not,\" he said. He expects investors to become smarter and learn to distinguish between earnings growth through accrual accounting and growth fueled by mark-to-market accounting. At the end of the day, it is not a matter of simply producing profits, but being able to say where those earnings came from, said one investor, who manages a pension fund. Some investors also may be placing a greater emphasis on the cash flow the energy merchants produce. Tim O'Brien, portfolio manager of the Gabelli Utilities Fund, said energy merchants that own the physical power assets to back up their trading positions should trade at a premium to an independent power producers and traditional utility companies. Still, the stocks should be valued at less than the growth rate of the company because of their heavy exposures to commodity prices. Energy merchants include companies such as Dynegy Inc. (DYN), Duke Energy Corp. (DUK) and Dominion Resources Inc. (D). According to O'Brien, the group never deserved to have the price-to-earnings multiples above 20- to 30-times earnings, which were once paid for the stocks. \"We all got sucked up by the up-leg of the cycle and forgot just how cyclical these companies are,\" O'Brien said, adding that the average multiple should be in the high single-digits to the high-teens.\""},
{"reason":"The email discusses mark-to-market accounting practices and their potential impact on earnings, but does not indicate any abuse or attempt to hide losses."},
{"Score":0}"""
score(tmp)

(0,
 'The email discusses mark-to-market accounting practices and their potential impact on earnings, but does not indicate any abuse or attempt to hide losses')

In [56]:
import json
for i in tmp.split('}'):
    j=i[3:].split(':')
    if 'reason' in j[0]:
        print(j[1][1:-1])
    if 'Score' in j[0]:
        print(j[1])

The email discusses mark-to-market accounting practices and their potential impact on earnings, but does not indicate any abuse or attempt to hide losses.
0


In [82]:
scoreEmails(test_df)
test_df.to_csv("llama3.csv")

Querying llm
Querying llm llama3
4661 2770 Investors are asking hard questions, and not always getting the answers they want. Using mark-to-market methods, a company calculates the fair market value of a commodity position - whether it's a contract, an option, a swap, etc. - at the time, even if the value of the position is realized over a longer period. The problem with this method is the actual cash a company realizes from the position might not be the same value the company calculated in its original assessment. Also, sometimes it isn't easy to calculate the fair value of the commodity position. This is particularly true in instances where the market for the commodity isn't liquid. Over time, companies with the highest level of disclosure regarding their mark-to-market gains will most likely trade at higher multiples to counterparts that provide little or no disclosure, said ABN AMRO Inc. analyst Paul Patterson. Encouragingly, it appears companies may already be responding to the ca

/var/folders/b5/q7jfctvs3wl6sly80nxcpg3h0000gn/T/ipykernel_19939/800824971.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_df.loc[test_df.index == i, f'{model}_result'] =x


Here is the output in JSON format:

[{"email_text":"Subject: The first detailed allegations that Enron abused mark-to-market accounting to hide wholesale trading losses have emerged in congressional testimony provided by a professor and former derivative trader who reviewed the Enron case for Senate Governmental Affairs Committee. Those charges, along with allegations that have surfaced that mark-to-market accounting was misused by Enron Energy Services, the company's retail energy and services unit, are expected to support the push by accounting rule-makers for much more disclosure on mark-to-market accounting practices and the impact of mark-to-market accounting on earnings trading firms' earnings. In testimony Thursday before the Senate Governmental Affairs Committee last week, Frank Partnoy of the University of San Diego Law School, said it appears that Enron traders mismarked forward curves and manipulated the amount of profits and losses that would be reported in financial statem

In [83]:
test_df

search_phrase  label  \
10    mark to market accounting practices      1   
13    mark to market accounting practices      1   
15    mark to market accounting practices      1   
18    mark to market accounting practices      1   
22    mark to market accounting practices      1   
...                                   ...    ...   
1817                               RANDOM      1   
2151                               RANDOM      1   
2506                               RANDOM      1   
2507                               RANDOM      1   
2508                               RANDOM      1   

                                                  email  mistral_pred  \
10    Investors are asking hard questions, and not a...           0.0   
13    Subject: The first detailed allegations that E...           1.0   
15    ancial reporting technique called mark-to-mark...           1.0   
18    ng more disclosures about the accounting used,...           0.7   
22    "There could be a quality-of-earnings issue," ...           0.5   
...                                                 ...           ...   
1817  Subject: bookouts in discussion\n\nBill,\n\nPe...           0.0   
2151  Subject: \n\nMark, this is great - giving the ...           0.0   
2506  -bid & to prevent market manipulation.\n  \n  ...           0.5   
2507  n are causing loss to \nEnron by, what we beli...           0.5   
2508   London Commercial Court \ncould be swayed by ...           0.7   

      openhermes_pred  vicuna_pred  gemma_pred  \
10                0.0          0.7         0.2   
13                0.8          0.9         0.0   
15                0.7          0.9         0.8   
18                0.5          0.7         0.8   
22                0.5          0.8         0.2   
...               ...          ...         ...   
1817              0.0          0.7         0.2   
2151              0.0          0.7         0.0   
2506              0.0          0.8         0.6   
2507              0.5          0.9         0.6   
2508              0.0          0.8         0.6   

                                           qwen2_result  \
10    The email does not indicate any specific actio...   
13    [\n    {"email_text": "Subject: The first deta...   
15    ```json\n{\n    "email_text": "anical reportin...   
18    ```json\n{\n    "email_text": "ng more disclos...   
22    {"email_text":"There could be a quality-of-ear...   
...                                                 ...   
1817                                                NaN   
2151                                                NaN   
2506                                                NaN   
2507                                                NaN   
2508                                                NaN   

                                          llama3_result  
10    Here is the output in JSON format:\n\n[{"email...  
13    Here is the output in JSON format:\n\n[{"email...  
15    Here is the output in JSON format:\n\n[{"email...  
18    Here is the output in JSON format:\n\n[{"email...  
22    Here is the output in JSON format:\n\n[{"email...  
...                                                 ...  
1817  Here is the output in JSON format:\n\n[{"email...  
2151  Here is the output in JSON format:\n\n[{"email...  
2506  Here is the output in JSON format:\n\n[{"email...  
2507  Here is the output in JSON format:\n\n[{"email...  
2508  Here is the output in JSON format:\n\n[{"email...  

[391 rows x 9 columns]

In [84]:
scoreEmails(test_df,model="gemma2")
test_df.to_csv("gemma2.csv")

Querying llm
Querying llm gemma2
4661 2770 Investors are asking hard questions, and not always getting the answers they want. Using mark-to-market methods, a company calculates the fair market value of a commodity position - whether it's a contract, an option, a swap, etc. - at the time, even if the value of the position is realized over a longer period. The problem with this method is the actual cash a company realizes from the position might not be the same value the company calculated in its original assessment. Also, sometimes it isn't easy to calculate the fair value of the commodity position. This is particularly true in instances where the market for the commodity isn't liquid. Over time, companies with the highest level of disclosure regarding their mark-to-market gains will most likely trade at higher multiples to counterparts that provide little or no disclosure, said ABN AMRO Inc. analyst Paul Patterson. Encouragingly, it appears companies may already be responding to the ca

/var/folders/b5/q7jfctvs3wl6sly80nxcpg3h0000gn/T/ipykernel_19939/800824971.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_df.loc[test_df.index == i, f'{model}_result'] =x


```json
[
  {
    "email_text": "Subject: The first detailed allegations that Enron abused mark-to-market accounting to hide wholesale trading losses have emerged in congressional testimony provided by a professor and former derivative trader who reviewed the Enron case for Senate Governmental Affairs Committee. Those charges, along with allegations that have surfaced that mark-to-market accounting was misused by Enron Energy Services, the company's retail energy and services unit, are expected to support the push by accounting rulemakers for much more disclosure on mark-to-market accounting practices and the impact of mark-to-market accounting on earnings trading firms' earnings. In testimony Thursday before the Senate Governmental Affairs Committee last week, Frank Partnoy of the University of San Diego Law School, said it appears that Enron traders mismarked forward curves and manipulated the amount of profits and losses that would be reported in financial statements. In a nutshell,

In [85]:
scoreEmails(test_df,model="phi3")
test_df.to_csv("phi3.csv")

Querying llm
Querying llm phi3
4661 2770 Investors are asking hard questions, and not always getting the answers they want. Using mark-to-market methods, a company calculates the fair market value of a commodity position - whether it's a contract, an option, a swap, etc. - at the time, even if the value of the position is realized over a longer period. The problem with this method is the actual cash a company realizes from the position might not be the same value the company calculated in its original assessment. Also, sometimes it isn't easy to calculate the fair value of the commodity position. This is particularly true in instances where the market for the commodity isn't liquid. Over time, companies with the highest level of disclosure regarding their mark-to-market gains will most likely trade at higher multiples to counterparts that provide little or no disclosure, said ABN AMRO Inc. analyst Paul Patterson. Encouragingly, it appears companies may already be responding to the call

/var/folders/b5/q7jfctvs3wl6sly80nxcpg3h0000gn/T/ipykernel_19939/800824971.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_df.loc[test_df.index == i, f'{model}_result'] =x


```json
[
    {
        "email_text": "Subject: The first detailed allegations that Enron abused mark-to-market accounting to hide wholesale trading losses have emerged in congressional testimony provided by a professor and former derivatives trader who reviewed the Enron case for Senate Governmental Affairs Committee. Those charges, along with allegations that mark-to-market accounting was misused by Enron Energy Services, the company's retail energy and services unit, are expected to support the push by accounting rulemakers for much more disclosure on mark-to-market accounting practices and the impact of mark-to-market accounting on earnings trading firms' earnings. In testimony last week before the Senate Governmental Affairs Committee, Frank Partnoy of the University of San Diego Law School said it appears that Enron employees used dummy accounts and rigged valuation methodologies to create false profit-and-loss entries for the derivatives Enron traded. 'Traders are compensated ba

In [86]:
scoreEmails(test_df,model="mistral")
test_df.to_csv("mistral.csv")

Querying llm
Querying llm mistral
4661 2770 Investors are asking hard questions, and not always getting the answers they want. Using mark-to-market methods, a company calculates the fair market value of a commodity position - whether it's a contract, an option, a swap, etc. - at the time, even if the value of the position is realized over a longer period. The problem with this method is the actual cash a company realizes from the position might not be the same value the company calculated in its original assessment. Also, sometimes it isn't easy to calculate the fair value of the commodity position. This is particularly true in instances where the market for the commodity isn't liquid. Over time, companies with the highest level of disclosure regarding their mark-to-market gains will most likely trade at higher multiples to counterparts that provide little or no disclosure, said ABN AMRO Inc. analyst Paul Patterson. Encouragingly, it appears companies may already be responding to the c

/var/folders/b5/q7jfctvs3wl6sly80nxcpg3h0000gn/T/ipykernel_19939/800824971.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_df.loc[test_df.index == i, f'{model}_result'] =x


 [{"email_text":"Subject: The first detailed allegations that Enron abused mark-to-market accounting to hide wholesale trading losses have emerged in congressional testimony provided by a professor and former derivatives trader who reviewed the Enron case for Senate Governmental Affairs Committee. Those charges, along with allegations that have surfaced that mark-to-market accounting was misused by Enron Energy Services, the company's retail energy and services unit, are expected to support the push by accounting rule makers for much more disclosure on mark-to-market accounting practices and the impact of mark-to-market accounting on earnings trading firms' earnings. In testimony Thursday before the Senate Governmental Affairs Committee last week, Frank Partnoy of the University of San Diego Law School, said it appears that Enron traders mismarked forward curves and manipulated the amount of profits and losses that would be reported in financial statements.",
"reason":"The email discus

In [87]:
scoreEmails(test_df,model="qwen2")
test_df.to_csv("qwen2.csv")

Querying llm
Querying llm qwen2
4661 2770 Investors are asking hard questions, and not always getting the answers they want. Using mark-to-market methods, a company calculates the fair market value of a commodity position - whether it's a contract, an option, a swap, etc. - at the time, even if the value of the position is realized over a longer period. The problem with this method is the actual cash a company realizes from the position might not be the same value the company calculated in its original assessment. Also, sometimes it isn't easy to calculate the fair value of the commodity position. This is particularly true in instances where the market for the commodity isn't liquid. Over time, companies with the highest level of disclosure regarding their mark-to-market gains will most likely trade at higher multiples to counterparts that provide little or no disclosure, said ABN AMRO Inc. analyst Paul Patterson. Encouragingly, it appears companies may already be responding to the cal

In [88]:
import pandas as pd
%whos DataFrame

Variable     Type         Data/Info
-----------------------------------
results_df   DataFrame                             <...>\n[2795 rows x 7 columns]
test_df      DataFrame                             <...>\n[391 rows x 12 columns]


In [89]:
test_df.columns

Index(['search_phrase', 'label', 'email', 'mistral_pred', 'openhermes_pred',
       'vicuna_pred', 'gemma_pred', 'qwen2_result', 'llama3_result',
       'gemma2_result', 'phi3_result', 'mistral_result'],
      dtype='object')

In [90]:
for i,j in test_df.iterrows():
    break
print(j['gemma2_result'])

```json
[
  {
    "email_text": "Investors are asking hard questions, and not always getting the answers they want. Using mark-to-market methods, a company calculates the fair market value of a commodity position - whether it's a contract, an option, a swap, etc. - at the time, even if the value of the position is realized over a longer period. The problem with this method is the actual cash a company realizes from the position might not be the same value the company calculated in its original assessment. Also, sometimes it isn't easy to calculate the fair value of the commodity position. This is particularly true in instances where the market for the commodity isn't liquid. Over time, companies with the highest level of disclosure regarding their mark-to-market gains will most likely trade at higher multiples to counterparts that provide little or no disclosure, said ABN AMRO Inc. analyst Paul Patterson. Encouragingly, it appears companies may already be responding to the call for add

In [100]:
def extract(j,model):
    xx=j[f'{model}_result']
    x1=xx.find('[')
    x2=xx.find(']')
    y=json.loads(xx[x1:x2+1])
    return y[0]['reason'],y[0]['Score']

In [103]:
j.index

Index(['search_phrase', 'label', 'email', 'mistral_pred', 'openhermes_pred',
       'vicuna_pred', 'gemma_pred', 'qwen2_result', 'llama3_result',
       'gemma2_result', 'phi3_result', 'mistral_result'],
      dtype='object')

In [99]:
j

search_phrase                    mark to market accounting practices
label                                                              1
email              Investors are asking hard questions, and not a...
mistral_pred                                                     0.0
openhermes_pred                                                  0.0
vicuna_pred                                                      0.7
gemma_pred                                                       0.2
qwen2_result       Here is a JSON format response for the provide...
llama3_result      Here is the output in JSON format:\n\n[{"email...
gemma2_result      ```json\n[\n  {\n    "email_text": "Investors ...
phi3_result        ```json\n[\n    {\n        "email_text": "Inve...
mistral_result      [{"email_text":"Investors are asking hard que...
Name: 10, dtype: object